In [1]:
# Copyright 2024 Keysight Technologies Inc.

In [2]:
import keysight.qcs as qcs

# initialize a qubit and an array to hold results
qubit = qcs.Qudits([0])

# define a program
program_in = qcs.Program()
program_in.add_gate(qcs.GATES.x, qubit)
program_in.add_measurement(qubit)

program_in.draw()

In [3]:
# define the replacement in terms of a pulse and channel
pulse = qcs.RFWaveform(
    duration=8e-8, envelope=qcs.GaussianEnvelope(), amplitude=1, rf_frequency=5e9
)

channel = qcs.Channels(range(1), "control_channel")

replacement_gt = qcs.Program()
replacement_gt.add_waveform(pulse, channel)

# specify the instruction to be replaced and create the Linker
linker_gt = qcs.Linker(qcs.GATES.x, qubit, replacement_gt)

In [4]:
replacement_meas = qcs.Program()
integration_filter = qcs.IntegrationFilter(pulse)
classifier = qcs.Classifier([0.0, 1.0])
replacement_meas.add_acquisition(integration_filter, channel, classifier)

linker_meas = qcs.ParameterizedLinker(qcs.Measure(), qubit, replacement_meas)

In [5]:
program_out = qcs.Executor(qcs.LinkerPass(linker_gt, linker_meas)).execute(program_in)

In [6]:
program_out.draw()

In [7]:
program = qcs.Program()
program.add_measurement(qubit, reset=True, repeat_reset=2)
program.draw()

In [8]:
replacement_id = qcs.Program()
replacement_id.add_waveform(qcs.Delay(0), channel)

linker_id = qcs.Linker(qcs.GATES.id, qubit, replacement_id)

In [9]:
program_out = qcs.LinkerPass(linker_gt, linker_id, linker_meas).apply(program)
program_out.draw()